In [3]:
# coding: utf-8

# plasticity

from __future__ import absolute_import 
from __future__ import division 
from __future__ import print_function

import numpy as np 
import tensorflow as tf 
import pickle 
import os 
import calendar
import time
import argparse 
import sys 
import plas_resnet
import data

tf.logging.set_verbosity(tf.logging.INFO)

cifar10_path = '..\..\code\plasticity\Plasticity-Networks-master\cifar10-zty\divided_cifar10_data'
model_root = '..\..\code\plasticity\Plasticity-Networks-master\cifar10-zty\ckpts_5v5_plas'

#pretrained_model = '/scratch/tz1303/ckpts_5v5_plas/1537256622/pre_plas_res20-8500'

num_res_blocks = 3

#batchsize = 32
maxepochs = 100

_HEIGHT = 32 
_WIDTH = 32 
_NUM_CHANNELS = 3

classcount = 5 

use_val = 15

def make_model_dir():
    if not FLAGS.save_dir == 'default':
        model_dir = os.path.join(model_root, FLAGS.save_dir)
    else:
        timestamp = calendar.timegm(time.gmtime())
        model_dir = os.path.join(model_root, str(timestamp))
    if not os.path.exists(model_dir):
        os.makedirs(model_dir)
    tf.logging.info(model_dir)
    return model_dir

def train_layers(min_stack=0, first_min_block=0):
    train_scope = []
    
    min_block = first_min_block
    for stack in range(min_stack, 3):
        for res_block in range(min_block, num_res_blocks):
            train_scope.append("feature_extractor/{}_{}_one/".format(stack, res_block))

            train_scope.append("feature_extractor/{}_{}_two/".format(stack, res_block))
            if stack>0 and res_block == 0:
                train_scope.append("feature_extractor/{}_{}_three/".format(stack, res_block))
        min_block = 0      

    var = []
    if min_stack == 0:
        var.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, 'feature_extractor/first'))
    for scope in train_scope:
        var.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope))
    var.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, 'classifier'))
    train_var = [item for sublist in var for item in sublist]
    tf.logging.info('----train variables----')
    for item in train_var:
        tf.logging.info(item)

    return train_var

def load_layers(min_stack=0, first_min_block=0):
    train_scope = []
    
    min_block = first_min_block
    for stack in range(0, min_stack):
        for res_block in range(min_block, num_res_blocks):
            train_scope.append("feature_extractor/{}_{}_one/".format(stack, res_block))

            train_scope.append("feature_extractor/{}_{}_two/".format(stack, res_block))
            if stack>0 and res_block == 0:
                train_scope.append("feature_extractor/{}_{}_three/".format(stack, res_block))
        min_block = 0      

    var = []
    if min_stack > 0:
        var.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, 'feature_extractor/first'))
    for scope in train_scope:
        var.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope))
    train_var = [item for sublist in var for item in sublist]
    for item in train_var:
        tf.logging.info(item)

    return train_var

def trainable_var():
    var_names = []    
    for var in tf.trainable_variables():    
        var_names.append(var.name)
        print(var.name)

def lr_schedule(epoch):
    lr = 1e-3
    cond1 = tf.cond(tf.greater(epoch, 40), lambda:lr*1e-1, lambda:lr)
    cond2 = tf.cond(tf.greater(epoch, 60), lambda:lr*1e-2, lambda:cond1)
    cond3 = tf.cond(tf.greater(epoch, 80), lambda:lr*1e-3, lambda:cond2)
    cond4 = tf.cond(tf.greater(epoch, 90), lambda:lr*0.5e-3, lambda:cond3)
    cond4 = tf.identity(cond4, name='cond4')
    return cond4


def inference(transfer):
    tf.reset_default_graph()

    #-------------------------------------------------------------------------------------#
    train_dataset = data.train_input_fn(classcount=classcount, use_train=FLAGS.use_train, datapath=cifar10_path,
                                        dataset=FLAGS.dataset, batchsize=FLAGS.batchsize, maxepochs=maxepochs)
    train_iterator = train_dataset.make_one_shot_iterator()

    val_dataset = data.val_input_fn(classcount=classcount, use_val=use_val, datapath=cifar10_path,
                                    dataset=FLAGS.dataset, batchsize=FLAGS.batchsize, maxepochs=maxepochs)
    val_iterator = val_dataset.make_initializable_iterator()
    #-------------------------------------------------------------------------------------%

    handle = tf.placeholder(tf.string, shape=[])
    iterator = tf.contrib.data.Iterator.from_string_handle(
        handle, train_dataset.output_types, train_dataset.output_shapes)
    features, labels = iterator.get_next()
    
    global_step=tf.get_variable('global_step',(), trainable=False, initializer=tf.zeros_initializer)
    
    epoch = tf.ceil(global_step*FLAGS.batchsize/FLAGS.use_train)
    epoch = tf.identity(epoch, name='epoch')
    #-------------------------------------------------------------------------------------#
    onehot_labels = tf.one_hot(tf.cast(labels, tf.int32), classcount)
    logits, update_ops = plas_resnet.resnet_model(features, onehot_labels, 'feature_extractor', num_res_blocks, classcount)
    logits = tf.identity(logits, 'logits')
    #-------------------------------------------------------------------------------------%
    loss = tf.nn.softmax_cross_entropy_with_logits(labels=onehot_labels, logits=logits)
    loss = tf.reduce_mean(loss)

    lr = lr_schedule(epoch)
    lr = tf.identity(lr, name='lr')
    optimizer = tf.train.AdamOptimizer(lr)
    #--------------------------------------------------------------------------------------#
    model_dir = make_model_dir()
    
    # transfer
    if transfer:
        train_var = train_layers(FLAGS.from_stack, 0)
        train_op = optimizer.minimize(loss=loss, global_step=global_step, var_list=train_var)
        model_name = model_dir+'/trans_plas_res'+str(6*num_res_blocks+2)
    # pretrain
    else:
        train_op = optimizer.minimize(loss=loss, global_step=global_step)
        model_name = model_dir+'/pre_plas_res'+str(6*num_res_blocks+2)    
    #-------------------------------------------------------------------------------------%
    classes = tf.argmax(input=logits, axis=1)
    correct_prediction = tf.equal(tf.cast(classes, tf.uint8), labels)
    acc = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
    acc = tf.identity(acc, name='accuracy_tensor')

    init_op = tf.global_variables_initializer()
        
    with tf.Session() as sess:
        sess.run(init_op)
    #-------------------------------------------------------------------------------------#
        saver = tf.train.Saver(max_to_keep=5)
        if transfer:
            restore_var_list = tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope='feature_extractor/')
            #restore_var_list.append(tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES, scope='classifier/hebb')[0])
            restore_var_list.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope='classifier/eta')[0])
            restore_var_list.append(tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope='classifier/alpha')[0])
            tf.logging.info('----load variables----')
            for item in restore_var_list:
                tf.logging.info(item)
            #var_list = load_layers(FLAGS.from_stack, 0)
            restorer = tf.train.Saver(var_list=restore_var_list)
            #util.init_from_checkpoint(pretrained_model, {'feature_extractor/':'transfer/'})
            restorer.restore(sess, pretrained_model)
    #-------------------------------------------------------------------------------------%
        train_handle = sess.run(train_iterator.string_handle())
        val_handle = sess.run(val_iterator.string_handle())
        
        while True:
            try:
                steps = tf.train.global_step(sess, global_step)
                co = tf.get_default_graph().get_tensor_by_name("classifier/co:0")
                hebbb = tf.get_default_graph().get_tensor_by_name("classifier/hebb:0")
                ops = [train_op, loss, epoch, acc, lr, update_ops, co, hebbb]
                _, lossvalue, epoch_num, accuracy, learning_rate, _, coo, hebbbb = sess.run(ops, feed_dict = {handle: train_handle})
                print(coo,hebbbb)
                if steps % 1 == 0:
                    tf.logging.info('epoch:'+str(epoch_num)+' step:'+str(steps)+' learning rate:'+str(learning_rate))
                    tf.logging.info('loss:'+str(lossvalue)+' batch accuracy:'+str(accuracy))
                if steps % FLAGS.eval_step == 0:
                    if not transfer:
                        saver.save(sess, model_name, global_step = steps)
                    evalutation(sess, val_iterator, correct_prediction, handle, val_handle)
                    
            except tf.errors.OutOfRangeError:
                break
        evalutation(sess, val_iterator, correct_prediction, handle, val_handle)
        
def evalutation(sess, val_iterator, correct_prediction, handle, val_handle):
    correct_sum = 0
    count = 0

    sess.run(val_iterator.initializer)
    while True:
        try:                            
            correct_prediction_value = sess.run(correct_prediction, feed_dict = {handle: val_handle})
            count += correct_prediction_value.shape[0]
            correct_sum += np.sum(correct_prediction_value)
        except tf.errors.OutOfRangeError:
            break

    tf.logging.info('eval accuracy:'+str(correct_sum/count))
        
if __name__ == '__main__':
    parser = argparse.ArgumentParser()
    parser.add_argument(
        '--save_dir',
        type=str,
        default='default')

    parser.add_argument(
        '--use_train',
        type=int,
        default='250')

    parser.add_argument(
        '--mode',
        type=str,
        default='pretrain')

    parser.add_argument(
        '--from_stack',
        type=int,
        default='0')

    parser.add_argument(
        '--dataset',
        type=int,
        default='1')    

    parser.add_argument(
        '--eval_step',
        type=int,
        default='1')

    parser.add_argument(
        '--batchsize',
        type=int,
        default='16')

    FLAGS, unparsed = parser.parse_known_args()
    tf.logging.info('plasticity: True')
    tf.logging.info('mode: '+str(FLAGS.mode))
    tf.logging.info('traing on dataset: '+str(FLAGS.dataset))
    tf.logging.info('use train: '+str(FLAGS.use_train))
    tf.logging.info('from stack: '+str(FLAGS.from_stack))
    tf.logging.info('model save dir: '+str(FLAGS.save_dir))
    tf.logging.info('eval step: '+str(FLAGS.eval_step))
    tf.logging.info('batch size: '+str(FLAGS.batchsize))

    if FLAGS.mode == 'transfer':
        transfer = True
    elif FLAGS.mode == 'pretrain':
        transfer = False
    else:
        raise ValueError('unknown mode')

    inference(transfer)

INFO:tensorflow:plasticity: True
INFO:tensorflow:mode: pretrain
INFO:tensorflow:traing on dataset: 1
INFO:tensorflow:use train: 250
INFO:tensorflow:from stack: 0
INFO:tensorflow:model save dir: default
INFO:tensorflow:eval step: 1
INFO:tensorflow:batch size: 16
Loading training data...
(25000, 32, 32, 3)
(25000,)
All data loaded
(250, 32, 32, 3)
(250,)
Loading testing data...
(5000, 32, 32, 3)
(5000,)
All data loaded
(15, 32, 32, 3)
(15,)
INFO:tensorflow:..\..\code\plasticity\Plasticity-Networks-master\cifar10-zty\ckpts_5v5_plas\1537683160
[[0.         0.05404842 0.         0.         0.        ]
 [0.         0.         0.         0.         0.11265053]
 [0.         0.         0.         0.         0.12702422]
 [0.         0.05774272 0.         0.         0.        ]
 [0.         0.         0.43072468 0.         0.        ]
 [0.         0.06081684 0.         0.         0.        ]
 [0.         0.         0.39898387 0.         0.        ]
 [0.         0.05488925 0.         0.         0.

INFO:tensorflow:loss:1.5597762 batch accuracy:0.3125
INFO:tensorflow:eval accuracy:0.26666666666666666
[[0.         0.20893386 0.         0.         0.        ]
 [0.         0.20924704 0.         0.         0.        ]
 [0.         0.         0.         0.22944434 0.        ]
 [0.13272744 0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.22526512]
 [0.         0.         0.21703911 0.         0.        ]
 [0.         0.         0.22577886 0.         0.        ]
 [0.         0.         0.         0.         0.21496347]
 [0.13028513 0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.2353603 ]
 [0.         0.         0.         0.2205619  0.        ]
 [0.         0.         0.         0.22781001 0.        ]
 [0.         0.         0.23200832 0.         0.        ]
 [0.12983157 0.         0.         0.         0.        ]
 [0.         0.         0.         0.22379886 0.        ]
 [0.1366908  0.         0. 

INFO:tensorflow:loss:1.6200426 batch accuracy:0.1875
INFO:tensorflow:eval accuracy:0.2
[[0.         0.         0.         0.23647049 0.        ]
 [0.         0.18087348 0.         0.         0.        ]
 [0.1611655  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.20030527]
 [0.         0.         0.2174491  0.         0.        ]
 [0.15679732 0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.22580998]
 [0.         0.         0.22102015 0.         0.        ]
 [0.         0.         0.23046274 0.         0.        ]
 [0.15429619 0.         0.         0.         0.        ]
 [0.         0.         0.         0.23747227 0.        ]
 [0.         0.         0.         0.         0.22607462]
 [0.         0.17561065 0.         0.         0.        ]
 [0.16096915 0.         0.         0.         0.        ]
 [0.         0.16158594 0.         0.         0.        ]
 [0.         0.         0.         0.245854

INFO:tensorflow:loss:1.5497117 batch accuracy:0.4375
INFO:tensorflow:eval accuracy:0.2
[[0.         0.         0.22537519 0.         0.        ]
 [0.1877258  0.         0.         0.         0.        ]
 [0.         0.         0.2086811  0.         0.        ]
 [0.1887536  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.19704472]
 [0.         0.         0.20959516 0.         0.        ]
 [0.         0.         0.         0.25118488 0.        ]
 [0.         0.         0.         0.25220174 0.        ]
 [0.         0.         0.         0.         0.19658832]
 [0.16871539 0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.20496713]
 [0.         0.         0.20678852 0.         0.        ]
 [0.17761317 0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.19523075]
 [0.18942875 0.         0.         0.         0.        ]
 [0.         0.         0.         0.253754

INFO:tensorflow:loss:1.5561256 batch accuracy:0.25
INFO:tensorflow:eval accuracy:0.2
[[0.         0.         0.         0.2522966  0.        ]
 [0.         0.         0.2086344  0.         0.        ]
 [0.22360888 0.         0.         0.         0.        ]
 [0.         0.         0.         0.25157875 0.        ]
 [0.         0.14970809 0.         0.         0.        ]
 [0.         0.         0.         0.2536301  0.        ]
 [0.         0.         0.19854677 0.         0.        ]
 [0.         0.         0.         0.2523922  0.        ]
 [0.22025464 0.         0.         0.         0.        ]
 [0.         0.         0.22709225 0.         0.        ]
 [0.2168538  0.         0.         0.         0.        ]
 [0.         0.         0.         0.24418555 0.        ]
 [0.         0.         0.22852199 0.         0.        ]
 [0.         0.         0.         0.2549572  0.        ]
 [0.         0.         0.         0.2553657  0.        ]
 [0.         0.         0.         0.25508112

...

INFO:tensorflow:loss:0.8995935 batch accuracy:0.6875
INFO:tensorflow:eval accuracy:0.4666666666666667
[[0.         0.         0.07653072 0.         0.        ]
 [0.         0.         0.         0.52249473 0.        ]
 [0.         0.6582581  0.         0.         0.        ]
 [0.         0.         0.         0.         0.2925214 ]
 [0.         0.         0.         0.7153755  0.        ]
 [0.         0.9492245  0.         0.         0.        ]
 [0.         0.         0.         0.8284112  0.        ]
 [0.         0.17893839 0.         0.         0.        ]
 [0.         0.         0.         0.724464   0.        ]
 [0.         0.         0.6864309  0.         0.        ]
 [0.         0.9904068  0.         0.         0.        ]
 [0.         0.         0.         0.         0.35698965]
 [0.         0.         0.9005391  0.         0.        ]
 [0.6825474  0.         0.         0.         0.        ]
 [0.         0.99175054 0.         0.         0.        ]
 [0.         0.6246644  0.  

INFO:tensorflow:loss:0.7210511 batch accuracy:0.6875
INFO:tensorflow:eval accuracy:0.4666666666666667
[[0.72389466 0.         0.         0.         0.        ]
 [0.         0.         0.73163    0.         0.        ]
 [0.         0.         0.         0.5756654  0.        ]
 [0.         0.502389   0.         0.         0.        ]
 [0.         0.         0.         0.         0.2354233 ]
 [0.         0.         0.         0.         0.5366292 ]
 [0.         0.         0.         0.4705638  0.        ]
 [0.         0.         0.86104006 0.         0.        ]
 [0.         0.         0.         0.         0.7208197 ]
 [0.         0.         0.         0.         0.12676863]
 [0.         0.         0.7293797  0.         0.        ]
 [0.         0.         0.         0.43850932 0.        ]
 [0.         0.         0.         0.         0.02245712]
 [0.         0.         0.25200108 0.         0.        ]
 [0.5094179  0.         0.         0.         0.        ]
 [0.         0.         0.  

INFO:tensorflow:loss:1.1085 batch accuracy:0.5
INFO:tensorflow:eval accuracy:0.4666666666666667
[[0.         0.         0.         0.55243266 0.        ]
 [0.         0.         0.         0.         0.22280432]
 [0.59904146 0.         0.         0.         0.        ]
 [0.         0.         0.         0.6393876  0.        ]
 [0.         0.         0.         0.         0.8486754 ]
 [0.         0.         0.         0.37410048 0.        ]
 [0.         0.         0.         0.         0.8537989 ]
 [0.         0.         0.         0.5613156  0.        ]
 [0.5700377  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.6861084 ]
 [0.         0.         0.         0.         0.97165483]
 [0.         0.         0.74955267 0.         0.        ]
 [0.         0.999778   0.         0.         0.        ]
 [0.         0.11939241 0.         0.         0.        ]
 [0.         0.         0.         0.         0.471031  ]
 [0.         0.         0.97160023

INFO:tensorflow:loss:0.9669424 batch accuracy:0.5625
INFO:tensorflow:eval accuracy:0.4666666666666667
[[0.         0.         0.         0.         0.08104699]
 [0.7457455  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.16348197]
 [0.         0.7316032  0.         0.         0.        ]
 [0.         0.         0.         0.         0.46995077]
 [0.         0.         0.         0.6528719  0.        ]
 [0.         0.         0.         0.43532407 0.        ]
 [0.         0.         0.         0.7552473  0.        ]
 [0.         0.         0.652296   0.         0.        ]
 [0.5232658  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.2775935 ]
 [0.         0.         0.3085138  0.         0.        ]
 [0.11192231 0.         0.         0.         0.        ]
 [0.         0.         0.24062122 0.         0.        ]
 [0.         0.         0.49133152 0.         0.        ]
 [0.45296142 0.         0.  

KeyboardInterrupt: 